# Games - Analysis of Advertising Sources

## Additionally

Dashboards:

https://public.tableau.com/profile/elina8438#!/vizhome/Mobile_game_dash/Dashboard1?publish=yes
    
    

### A task**:**

Analyze the behavior of players depending on the source of the transition.

## 1. General information: 

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns 
import matplotlib.pyplot as plt
import datetime
import math as mth
from scipy import stats as st
import plotly
import plotly.express as px
from plotly import graph_objects as go
from plotly.offline import iplot
import decimal
import warnings
warnings.filterwarnings('ignore')

In [2]:
ad_costs = pd.read_csv('ad_costs.csv')

In [3]:
ad_costs.head(10)

source         day        cost
0           facebook_ads  2020-05-03  935.882786
1           facebook_ads  2020-05-04  548.354480
2           facebook_ads  2020-05-05  260.185754
3           facebook_ads  2020-05-06  177.982200
4           facebook_ads  2020-05-07  111.766796
5           facebook_ads  2020-05-08   68.009276
6           facebook_ads  2020-05-09   38.723350
7  instagram_new_adverts  2020-05-03  943.204717
8  instagram_new_adverts  2020-05-04  502.925451
9  instagram_new_adverts  2020-05-05  313.970984

In [4]:
game_actions = pd.read_csv('game_actions.csv')

In [5]:
game_actions.head(10)

event_datetime     event  building_type  \
0  2020-05-04 00:00:01  building  assembly_shop   
1  2020-05-04 00:00:03  building  assembly_shop   
2  2020-05-04 00:00:16  building  assembly_shop   
3  2020-05-04 00:00:16  building  assembly_shop   
4  2020-05-04 00:00:35  building  assembly_shop   
5  2020-05-04 00:00:36  building  assembly_shop   
6  2020-05-04 00:00:36  building  assembly_shop   
7  2020-05-04 00:00:38  building  assembly_shop   
8  2020-05-04 00:00:44  building  assembly_shop   
9  2020-05-04 00:01:33  building  assembly_shop   

                                user_id project_type  
0  55e92310-cb8e-4754-b622-597e124b03de          NaN  
1  c07b1c10-f477-44dc-81dc-ec82254b1347          NaN  
2  6edd42cc-e753-4ff6-a947-2107cd560710          NaN  
3  92c69003-d60a-444a-827f-8cc51bf6bf4c          NaN  
4  cdc6bb92-0ccb-4490-9866-ef142f09139d          NaN  
5  06c592ca-902d-42bb-bac3-75ce84cca159          NaN  
6  4fe0f101-694b-4e31-9740-d1d87f7208ea          NaN  
7  beb8ca15-33a9-465d-b47b-89aa96f89c9a          NaN  
8  65a92713-5969-48b1-8945-bfefa5063887          NaN  
9  fa352362-d258-472c-b295-2796ccc39fa3          NaN

In [6]:
user_source = pd.read_csv('user_source.csv')

In [7]:
user_source.head(10)

user_id                   source
0  0001f83c-c6ac-4621-b7f0-8a28b283ac30             facebook_ads
1  00151b4f-ba38-44a8-a650-d7cf130a0105            yandex_direct
2  001aaea6-3d14-43f1-8ca8-7f48820f17aa  youtube_channel_reklama
3  001d39dc-366c-4021-9604-6a3b9ff01e25    instagram_new_adverts
4  002f508f-67b6-479f-814b-b05f00d4e995             facebook_ads
5  003b80c6-4164-4157-bb2a-03d0181d39c4            yandex_direct
6  003ee7e8-6356-4286-a715-62f22a18d2a1    instagram_new_adverts
7  004074f8-251a-4776-922c-8348dca1a2f6             facebook_ads
8  00440efd-aa50-4b4b-aae8-ffcd1782729d             facebook_ads
9  00464e5e-28ed-4be6-bf44-517ef7b3937b            yandex_direct

## 2. Data preprocessing:

In [8]:
ad_costs.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 28 entries, 0 to 27
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   source  28 non-null     object 
 1   day     28 non-null     object 
 2   cost    28 non-null     float64
dtypes: float64(1), object(2)
memory usage: 800.0+ bytes


In [9]:
ad_costs.duplicated().sum()

0

In [10]:
ad_costs.rename(columns={"day": "date"},inplace=True)

In [11]:
ad_costs['date'] = pd.to_datetime(ad_costs['date'])

In [12]:
game_actions.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 135640 entries, 0 to 135639
Data columns (total 5 columns):
 #   Column          Non-Null Count   Dtype 
---  ------          --------------   ----- 
 0   event_datetime  135640 non-null  object
 1   event           135640 non-null  object
 2   building_type   127957 non-null  object
 3   user_id         135640 non-null  object
 4   project_type    1866 non-null    object
dtypes: object(5)
memory usage: 5.2+ MB


In [13]:
game_actions[game_actions['building_type'].isna()]['event'].value_counts()

finished_stage_1    5817
project             1866
Name: event, dtype: int64

In the `project_type` column, gaps appear if the player has not yet completed the level in any of the ways.

In [14]:
game_actions['event_datetime'] = pd.to_datetime(game_actions['event_datetime'])

In [15]:
game_actions.duplicated().sum()

1

In [16]:
game_actions[game_actions.duplicated(keep=False)]

event_datetime     event    building_type  \
74890 2020-05-10 18:41:56  building  research_center   
74891 2020-05-10 18:41:56  building  research_center   

                                    user_id project_type  
74890  c9af55d2-b0ae-4bb4-b3d5-f32aa9ac03af          NaN  
74891  c9af55d2-b0ae-4bb4-b3d5-f32aa9ac03af          NaN

Две одинаковые строки, одгу из которых можно смело удалять. 

In [17]:
game_actions = game_actions.drop_duplicates()

In [18]:
user_source.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13576 entries, 0 to 13575
Data columns (total 2 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   user_id  13576 non-null  object
 1   source   13576 non-null  object
dtypes: object(2)
memory usage: 212.2+ KB


In [19]:
user_source.duplicated().sum()

0

## 3. EDA

In [20]:
print('The number os users:', game_actions['user_id'].count())

The number os users: 135639


Consider the players who completed the first level.

In [21]:
users_events = game_actions.groupby('event')['user_id'].count().reset_index()
users_events 

event  user_id
0          building   127956
1  finished_stage_1     5817
2           project     1866

In [22]:
labels = ['building','finished_stage_1','project']
values = [127956, 3951, 1866]

fig = go.Figure(data=[go.Pie(labels=labels, values=values)])
fig.update_layout(
    title='Событий по количеству пользователей')
fig.show()

The most popular events: 

In [23]:
building_types = game_actions.groupby('building_type')['user_id'].count().reset_index().sort_values(by='user_id', ascending=False)
building_types
fig = go.Figure(data=[go.Pie(labels=building_types['building_type'], 
                             values = building_types['user_id'])]
                               )
fig.update_layout(
    title='Соотношение типов зданий')
fig.show()

In [24]:
ev_type = game_actions.groupby('user_id').agg({'event':'nunique'}).reset_index()

In [25]:
ev_1 = ev_type.query('event == 1')['user_id']
ev_2 = ev_type.query('event == 2')['user_id']
ev_3 = ev_type.query('event == 3')['user_id']

not_finished = game_actions.query('user_id in @ev_1')
vic = game_actions.query('user_id in @ev_2')
proj = game_actions.query('user_id in @ev_3')


In [26]:
won = vic.query('event != "building"') 
pjc = proj.query('event == "project"') 

In [27]:
won_pjc = pd.concat([won,pjc]).reset_index()

In [28]:
won_pjc

index      event_datetime             event building_type  \
0       6659 2020-05-04 19:47:29  finished_stage_1           NaN   
1      13134 2020-05-05 13:22:09  finished_stage_1           NaN   
2      15274 2020-05-05 18:54:37  finished_stage_1           NaN   
3      16284 2020-05-05 21:27:29  finished_stage_1           NaN   
4      19650 2020-05-06 06:02:22  finished_stage_1           NaN   
...      ...                 ...               ...           ...   
5812  135602 2020-06-02 03:04:42           project           NaN   
5813  135603 2020-06-02 06:21:03           project           NaN   
5814  135609 2020-06-02 17:17:28           project           NaN   
5815  135617 2020-06-03 09:46:04           project           NaN   
5816  135630 2020-06-04 08:29:42           project           NaN   

                                   user_id                project_type  
0     ced7b368-818f-48f6-9461-2346de0892c5                         NaN  
1     7ef7fc89-2779-46ea-b328-9e5035b83af5                         NaN  
2     70db22b3-c2f4-43bc-94ea-51c8d2904a29                         NaN  
3     903fc9ef-ba97-4b12-9d5c-ac8d602fbd8b                         NaN  
4     58e077ba-feb1-4556-a5a0-d96bd04efa39                         NaN  
...                                    ...                         ...  
5812  9d98001c-7e14-40d7-896e-46b3047365fd  satellite_orbital_assembly  
5813  df4a1e13-eba9-4928-a7cf-ee303d6f80f9  satellite_orbital_assembly  
5814  82e46f34-e243-4728-8e20-2e171fc33ea4  satellite_orbital_assembly  
5815  fe032991-71e0-48c5-889f-4c3805ba4c9b  satellite_orbital_assembly  
5816  d477dde8-7c22-4f23-9c4f-4ec31a1aa4c8  satellite_orbital_assembly  

[5817 rows x 6 columns]

In [29]:
finished_1_lvl = won_pjc.groupby('event')['user_id'].count().reset_index().sort_values(by='user_id', ascending=False)
finished_1_lvl
fig = go.Figure(data=[go.Pie(labels=finished_1_lvl['event'], 
                             values = finished_1_lvl['user_id'])]
                               )
fig.update_layout(
    title='Распределение пользователей по стратегии')
fig.show()

In [30]:
users = game_actions.merge(user_source, on='user_id') 
users

event_datetime     event  building_type  \
0      2020-05-04 00:00:01  building  assembly_shop   
1      2020-05-05 05:20:15  building  assembly_shop   
2      2020-05-05 19:24:02  building  assembly_shop   
3      2020-05-05 20:59:19  building  assembly_shop   
4      2020-05-06 00:52:56  building  assembly_shop   
...                    ...       ...            ...   
135634 2020-05-13 23:56:39  building      spaceport   
135635 2020-05-18 00:23:28  building      spaceport   
135636 2020-05-10 23:59:52  building  assembly_shop   
135637 2020-05-13 08:11:19  building      spaceport   
135638 2020-05-18 11:11:11  building      spaceport   

                                     user_id project_type  \
0       55e92310-cb8e-4754-b622-597e124b03de          NaN   
1       55e92310-cb8e-4754-b622-597e124b03de          NaN   
2       55e92310-cb8e-4754-b622-597e124b03de          NaN   
3       55e92310-cb8e-4754-b622-597e124b03de          NaN   
4       55e92310-cb8e-4754-b622-597e124b03de          NaN   
...                                      ...          ...   
135634  cafd1b8b-507b-49ae-abf0-89fe863a8b03          NaN   
135635  cafd1b8b-507b-49ae-abf0-89fe863a8b03          NaN   
135636  bdc53e19-462a-4dc3-8b55-b4a34278af6a          NaN   
135637  bdc53e19-462a-4dc3-8b55-b4a34278af6a          NaN   
135638  bdc53e19-462a-4dc3-8b55-b4a34278af6a          NaN   

                         source  
0       youtube_channel_reklama  
1       youtube_channel_reklama  
2       youtube_channel_reklama  
3       youtube_channel_reklama  
4       youtube_channel_reklama  
...                         ...  
135634             facebook_ads  
135635             facebook_ads  
135636  youtube_channel_reklama  
135637  youtube_channel_reklama  
135638  youtube_channel_reklama  

[135639 rows x 6 columns]

In [31]:
cnt_source = users[users['event']!= 'building'].groupby('source')['user_id'].agg(user_id = 'count')  
cnt_source

user_id
source                          
facebook_ads                1541
instagram_new_adverts       1942
yandex_direct               2662
youtube_channel_reklama     1538

In [32]:
users_plot = users[users['event']!= 'building'].groupby(['source','event'])['user_id'].agg(user_id = 'nunique').sort_values('user_id', ascending = False).reset_index() 
final_users_plot = cnt_source.merge(users_plot, how='left', on='source')
final_users_plot.rename(columns={'user_id_x': 'users_total', 'user_id_y': 'users'}, inplace=True) 
final_users_plot['ratio_by_source'] =   final_users_plot['users']/ final_users_plot['users_total']
final_users_plot = final_users_plot.sort_values('ratio_by_source', ascending = False).reset_index() 
final_users_plot['ratio'] = round(final_users_plot['users'] / final_users_plot['users'].sum(), 2) 
final_users_plot

index                   source  users_total             event  users  \
0      4            yandex_direct         2662  finished_stage_1   2042   
1      2    instagram_new_adverts         1942  finished_stage_1   1466   
2      6  youtube_channel_reklama         1538  finished_stage_1   1159   
3      0             facebook_ads         1541  finished_stage_1   1150   
4      1             facebook_ads         1541           project    391   
5      7  youtube_channel_reklama         1538           project    379   
6      3    instagram_new_adverts         1942           project    476   
7      5            yandex_direct         2662           project    620   

   ratio_by_source  ratio  
0         0.767092   0.27  
1         0.754892   0.19  
2         0.753576   0.15  
3         0.746269   0.15  
4         0.253731   0.05  
5         0.246424   0.05  
6         0.245108   0.06  
7         0.232908   0.08

In [33]:
fig = px.bar(final_users_plot, 
             x="source",
             y="ratio_by_source", 
             color="event", 
             title="Распределение пользователей по источникам и способам прохождения уровня",
             labels={"ratio_by_source": "Количество пользователей, %.",  "source": "Источник, с которого пришёл пользователь"})
fig.show()

In [34]:
fig = px.bar(final_users_plot, 
             x="source",
             y="ratio", 
             color="event", 
             title="Распределение пользователей по источникам и способам прохождения уровня",
             labels={"ratio": "Количество пользователей, %.",  "source": "Источник, с которого пришёл пользователь"})
fig.show()

In [35]:
# users who completed level 1
game_actions['project_type'] = game_actions['project_type'].fillna('none')
# first event for user
first_user_action = game_actions.groupby('user_id')['event_datetime'].min().reset_index().rename(columns={'event_datetime':'first_action'})
# last event for user
last_user_action = game_actions.groupby('user_id')['event_datetime'].max().reset_index().rename(columns={'event_datetime':'last_action'})

# tables for merging
events_for_users = game_actions[['user_id', 'event_datetime', 'event']]
user_project_type = game_actions[['user_id', 'project_type']].query('project_type != "none"')

In [36]:
actions_for_users = (first_user_action
    .merge(last_user_action, how='left', on='user_id')
    .merge(events_for_users, how='left', left_on=['user_id', 'last_action'], right_on=['user_id', 'event_datetime'])
    .merge(user_project_type, how='left', on='user_id'))
    
actions_for_users['project_type'] = actions_for_users['project_type'].fillna('none')
actions_for_users['duration'] = actions_for_users['last_action'] - actions_for_users['first_action']
actions_for_users['days'] = actions_for_users['duration'].dt.days
actions_for_users.head()

user_id        first_action  \
0  0001f83c-c6ac-4621-b7f0-8a28b283ac30 2020-05-06 01:07:37   
1  00151b4f-ba38-44a8-a650-d7cf130a0105 2020-05-06 03:09:12   
2  001aaea6-3d14-43f1-8ca8-7f48820f17aa 2020-05-05 18:08:52   
3  001d39dc-366c-4021-9604-6a3b9ff01e25 2020-05-05 21:02:05   
4  002f508f-67b6-479f-814b-b05f00d4e995 2020-05-05 13:49:58   

          last_action      event_datetime             event project_type  \
0 2020-05-20 11:26:06 2020-05-20 11:26:06          building         none   
1 2020-05-18 10:46:52 2020-05-18 10:46:52          building         none   
2 2020-05-14 09:21:27 2020-05-14 09:21:27          building         none   
3 2020-05-12 07:40:47 2020-05-12 07:40:47  finished_stage_1         none   
4 2020-05-22 02:46:45 2020-05-22 02:46:45          building         none   

          duration  days  
0 14 days 10:18:29    14  
1 12 days 07:37:40    12  
2  8 days 15:12:35     8  
3  6 days 10:38:42     6  
4 16 days 12:56:47    16

In [37]:
%pylab

Using matplotlib backend: MacOSX
Populating the interactive namespace from numpy and matplotlib


In [38]:
# the number of players, who implemented the project
project = actions_for_users.query('project_type != "none"') 
fig = go.Figure(go.Histogram(x=project['days'], y=project['user_id']),)
fig.update_layout(
    title_text= "Распределение пользователей, реализовавших проект",
    xaxis_title_text='Количество пользователей, шт.', 
    yaxis_title_text='Продолжительность игры'
)
fig.show() 


In [39]:
# the number of players, who won the opponent
win = actions_for_users.query('project_type == "none" and event == "finished_stage_1"')
fig = go.Figure(data=[go.Histogram(x=win['days'], y=win['user_id']),])
fig.update_layout(
    title_text= "Распределение пользователей, совершивших победу над другим игроком",
    xaxis_title_text='Количество пользователей, шт.', 
    yaxis_title_text='Продолжительность игры'
)

fig.show() 


In [40]:
building_source = actions_for_users.merge(user_source, on='user_id') 
building_source.head()

user_id        first_action  \
0  0001f83c-c6ac-4621-b7f0-8a28b283ac30 2020-05-06 01:07:37   
1  00151b4f-ba38-44a8-a650-d7cf130a0105 2020-05-06 03:09:12   
2  001aaea6-3d14-43f1-8ca8-7f48820f17aa 2020-05-05 18:08:52   
3  001d39dc-366c-4021-9604-6a3b9ff01e25 2020-05-05 21:02:05   
4  002f508f-67b6-479f-814b-b05f00d4e995 2020-05-05 13:49:58   

          last_action      event_datetime             event project_type  \
0 2020-05-20 11:26:06 2020-05-20 11:26:06          building         none   
1 2020-05-18 10:46:52 2020-05-18 10:46:52          building         none   
2 2020-05-14 09:21:27 2020-05-14 09:21:27          building         none   
3 2020-05-12 07:40:47 2020-05-12 07:40:47  finished_stage_1         none   
4 2020-05-22 02:46:45 2020-05-22 02:46:45          building         none   

          duration  days                   source  
0 14 days 10:18:29    14             facebook_ads  
1 12 days 07:37:40    12            yandex_direct  
2  8 days 15:12:35     8  youtube_channel_reklama  
3  6 days 10:38:42     6    instagram_new_adverts  
4 16 days 12:56:47    16             facebook_ads

In [41]:
project_source = building_source.query('project_type != "none"') 

fig = px.histogram(project_source , x="days", 
                   y="user_id",
                   color="source",
                   title="Распределение пользователей, реализовавших проект (по источникам)")
                   #labels={"user_id": "Количество пользователей, шт.",  "days": "Продолжительность игры"})

fig.show()

In [42]:
win_source = building_source.query('project_type == "none" and event == "finished_stage_1"')

fig = px.histogram(win_source, x="days", 
                   y="user_id",
                   color = "source",
                   title="Распределение пользователей, совершивших победу над другим игроком (по источникам)")
                   #labels={"user_id": "Количество пользователей, шт.",  "days": "Продолжительность игры"})
fig.show() 

On average, the time of an object, regardless of the source, takes about 13 days. Defeating an enemy takes 11 days on average.


### Which object is being built more often and the number of buildings by source?

In [43]:
populap_building_types = users.groupby(['building_type', 'source'])['user_id'].agg(['count']).sort_values('source', ascending = False).reset_index() 
populap_building_types

building_type                   source  count
0     assembly_shop  youtube_channel_reklama  10651
1   research_center  youtube_channel_reklama   2703
2         spaceport  youtube_channel_reklama  11624
3     assembly_shop            yandex_direct  19295
4   research_center            yandex_direct   4952
5         spaceport            yandex_direct  20785
6     assembly_shop    instagram_new_adverts  13431
7   research_center    instagram_new_adverts   3537
8         spaceport    instagram_new_adverts  14847
9     assembly_shop             facebook_ads  11117
10  research_center             facebook_ads   2945
11        spaceport             facebook_ads  12069

In [44]:
cnt_building_type_source = users.loc[users['building_type'].notnull()].groupby(['source'])['user_id'].agg(['count']).reset_index() 
final_populap_building_types = cnt_building_type_source .merge(populap_building_types, how='left', on='source') 
final_populap_building_types.rename(columns={'count_x': 'users_total', 'count_y': 'users'}, inplace=True) 
final_populap_building_types = final_populap_building_types.sort_values(by = 'source').reset_index() 
final_populap_building_types['ratio_by_source'] = round(final_populap_building_types['users']/ final_populap_building_types['users_total'],3)
final_populap_building_types_cnt = final_populap_building_types.sort_values(by = 'users', ascending = False).reset_index()
final_populap_building_types

index                   source  users_total    building_type  users  \
0       0             facebook_ads        26131    assembly_shop  11117   
1       1             facebook_ads        26131  research_center   2945   
2       2             facebook_ads        26131        spaceport  12069   
3       3    instagram_new_adverts        31815    assembly_shop  13431   
4       4    instagram_new_adverts        31815  research_center   3537   
5       5    instagram_new_adverts        31815        spaceport  14847   
6       6            yandex_direct        45032    assembly_shop  19295   
7       7            yandex_direct        45032  research_center   4952   
8       8            yandex_direct        45032        spaceport  20785   
9       9  youtube_channel_reklama        24978    assembly_shop  10651   
10     10  youtube_channel_reklama        24978  research_center   2703   
11     11  youtube_channel_reklama        24978        spaceport  11624   

    ratio_by_source  
0             0.425  
1             0.113  
2             0.462  
3             0.422  
4             0.111  
5             0.467  
6             0.428  
7             0.110  
8             0.462  
9             0.426  
10            0.108  
11            0.465

In [45]:
fig = px.bar(final_populap_building_types_cnt,
             x='source',
             y='users',
             #orientation='h',
             color = 'building_type', 
             title='Популярность объектов по источникам',
             labels={"users": "Количество построек, шт.", "source": "Источник"})

fig.show() 

In [46]:
fig = px.bar(final_populap_building_types,
             x='source',
             y='ratio_by_source',
             #orientation='h',
             color = 'building_type', 
             title='Популярность объектов по источникам',
             labels={"ratio_by_source": "Количество построек, %", "source": "Источник"})

fig.show() 

In [47]:
game_actions['event_datetime'] = pd.to_datetime(game_actions['event_datetime'], format='%Y-%m-%d %H:%M:%S') 
game_actions['event_date'] = game_actions['event_datetime'].dt.date.astype('datetime64')

### How many users per day?

In [48]:
DAU = int(game_actions.groupby('event_date').agg({'user_id': 'nunique'}).mean())
print('Average number of unique users per day {} '.format(DAU))

Average number of unique users per day 2884 


In [49]:
game_actions['event_datetime'] = pd.to_datetime(game_actions['event_datetime'], format='%Y-%m-%d %H:%M:%S') 
game_actions['event_date'] = game_actions['event_datetime'].dt.date.astype('datetime64')
events_dau = game_actions.groupby('event_date').agg({'user_id': 'nunique'})
events_dau.plot(kind='bar', figsize=(15, 7))
plt.gca().set_xticklabels(events_dau.index.strftime('%d.%m'), rotation=90)
plt.title('DAU')
plt.ylabel('Уникальные пользователи, чел.')
plt.xlabel('Дни')
plt.show()

#### Retention Rate

In [50]:
first_activity_date = game_actions.groupby('user_id')['event_datetime'].min()
first_activity_date.name = 'first_session_month'
retention = game_actions.join(first_activity_date,on='user_id')
retention['first_session_month'] = retention['first_session_month'].astype('datetime64[D]')
retention['session_month'] = retention['event_datetime'].astype('datetime64[D]')
retention['cohort_lifetime'] = retention['session_month'] - retention['first_session_month']
retention['cohort_lifetime'] = retention['cohort_lifetime'] / np.timedelta64(1,'D')
retention['cohort_lifetime'] = retention['cohort_lifetime'].round().astype('int')
cohorts = (retention
                           .groupby(['first_session_month', 'cohort_lifetime'])
                           .agg({'user_id': 'nunique'})
                           .reset_index())

In [51]:
initial_users_count = cohorts[cohorts['cohort_lifetime']==0][['first_session_month', 'user_id']]
initial_users_count = initial_users_count.rename(columns={'user_id': 'cohort_users'})
cohorts = cohorts.merge(initial_users_count, on='first_session_month')
cohorts['retention'] = cohorts['user_id']/cohorts['cohort_users']
retention_pivot = cohorts.pivot_table(index='first_session_month', columns='cohort_lifetime',
                                          values='retention', aggfunc='sum')
retention_pivot.index = retention_pivot.index.strftime('%d.%m.%Y')

In [52]:
plt.figure(figsize=(20, 15))
plt.title('Удержание пользователей')
sns.heatmap(
    retention_pivot,
    annot=True, 
    fmt='.0%', 
    linewidths=1,
    linecolor='gray',
    robust=True,
    square=True,
    cbar=0
)
plt.yticks(rotation=0) 
plt.title('Состав когорт по отношению к первому дню жизни, %')
plt.xlabel('Lifetime когорты, дни')
plt.ylabel('Когорты')
plt.show()

#### CAC

In [53]:
CAC_cost = ad_costs.groupby('source')['cost'].agg(cost = 'sum') 
CAC_users = user_source.groupby('source')['user_id'].agg(user =  'count')  

In [54]:
CAC_per_user = CAC_cost.merge(CAC_users,left_index=True,right_index=True) 
CAC_per_user['cac'] = CAC_per_user['cost'] / CAC_per_user['user']    
CAC_per_user = CAC_per_user.sort_values('cac',ascending=False).reset_index()
CAC_per_user

source         cost  user       cac
0             facebook_ads  2140.904643  2726  0.785365
1    instagram_new_adverts  2161.441691  3347  0.645785
2            yandex_direct  2233.111449  4817  0.463590
3  youtube_channel_reklama  1068.119204  2686  0.397662

In [55]:
fig = px.bar(CAC_per_user, 
             y="source",
             x="cac", 
             orientation='h', 
             title="Затраты на привлечение игрока",
             labels={"cac": "Стоимость привлечения",  "source": "Источник, с которого пришёл пользователь"})
fig.show()

In [56]:
labels = CAC_per_user['source']
values = CAC_per_user['cost']
fig = go.Figure(data=[go.Pie(labels=labels, values=values, hole=.3)])
fig.update_layout(
    title='Маркетинговые затраты')
fig.show()

In [57]:
source_of_user = building_source.groupby('source')['user_id'].agg(user_id = 'nunique').sort_values('user_id', ascending = False).reset_index() 

In [58]:
fig = px.bar(source_of_user, 
             x="source",
             y="user_id", 
             title="Распределение пользователей по источникам",
             labels={"user_id": "Количество пользователей",  "source": "Источник, с которого пришёл пользователь"})
fig.show()

## Hypothesis testing

##### Hypothesis  №1

- H₀ there is NO difference in time of passing the level between users who completed the level by completing the project and users who completed the level by defeating another player
- H₁ THERE IS a difference in time of passing the level between users who completed the level through the implementation of the project, and users who completed the level by defeating another player

In [59]:
alpha = 0.05

results = st.ttest_ind(project['days'], win['days'], equal_var = False)
print('p-value: ', results.pvalue)

if (results.pvalue < alpha):
    print("Reject the null hypothesis")
else:
    print("Accept the null hypothesis")

p-value:  2.6237027268064204e-106
Reject the null hypothesis


In [60]:
print('Average time to complete a level through project implementation:' ,round(project['days'].mean()), 'days')

Average time to complete a level through project implementation: 13 days


In [61]:
print('Average time to complete a level through a victory over an opponent:' ,round(win['days'].mean()), 'days')

Average time to complete a level through a victory over an opponent: 11 days


##### Hypothesis №2

- H₀ there are NO differences in the number of buildings between users who finish the level through the implementation of the project, and users who finish the level by defeating another player
- H₁ THERE are differences in the number of buildings between users who finish the level through the implementation of the project, and users who finish the level by defeating another player

In [62]:
user_finished_stage_1 = game_actions.query('event != "building"')[['user_id', 'event']]
user_finished_stage_1.set_index('user_id', inplace=True)


building_cnt = game_actions.pivot_table(
    index='user_id',
    columns='building_type',
    values='event_date',
    aggfunc='count',
)
building_cnt['total'] = building_cnt.sum(axis=1)
user_building_activity = user_finished_stage_1.merge(
    building_cnt,
    how="left",
    left_index=True,
    right_index=True
)

In [63]:
cnt_building_pjc = user_building_activity[user_building_activity['event'] == 'project']

In [64]:
cnt_building_win = user_building_activity[user_building_activity['event'] != 'project']

In [65]:
alpha = 0.05

results = st.ttest_ind(cnt_building_pjc['total'], cnt_building_win['total'], equal_var = False)
print('p-value: ', results.pvalue)

if (results.pvalue < alpha):
    print("Reject the null hypothesis")
else:
    print("Accept the null hypothesis")

p-value:  3.624754689119661e-223
Reject the null hypothesis


In [66]:
print('Average number of objects built when passing a level through project implementation is :' ,round(cnt_building_pjc['total'].mean()), 'objects')

Average number of objects built when passing a level through project implementation is : 13 objects


In [67]:
print('Average number of objects built when passing a level through a victory over an opponent is:' ,round(cnt_building_win['total'].mean()), 'objects')

Average number of objects built when passing a level through a victory over an opponent is: 10 objects


## Conclusions 

During the analysis, we found out that the table contains information on 135,639 users. Of them:

- 1866 people finished the game with the implementation of the project
- 3951 people victory over the opponent.

The rest of the players are still in the process of passing the level. The average number of unique users per day is 2,884.

The most popular construction site is the spaceport, with over 46% of users building it.
The largest number of users came from the yandex source (among them 2042 users completed the level by fighting, 620 by the construction of an object), from the instagram source came (from 1466 they completed the level by battle and 476 by construction). Users from facebook and youtube sources were distributed about the same (1159 and 379 versus 1150 and 391).

The study is carried out for the period from 04.05 to 05.06, we observe the highest activity among users on day 7, when the number of users is about 10,000 people.

When calculating the rise in price, it was found that until 10 days most users are active, then there is a gradual decrease in activity. By day 23, activity is zero. We can say that the most favorable time is before 12 noon.

CAC:
- Facebook (0.79 y.e./person);
- Instagram (0.65 y.e./person);
- Yandex (0.46 y.e./person);
- YouTube (0.40 y.e./person).

Average time to completion of level 1
- Victory over the enemy, days: 11.
- Project implementation, days: 13.

Average number of buildings, depending on the method of passing the level:
- Victory over the enemy, days: 10.
- Project implementation, days: 13.


## Recommendations


Marketers need to make a decision about the frequency of their ads.
It is worth working on the popularity of passing the project, because these users spend more time at the level and build more buildings.

You can invest in various advertising banners, when viewed by users, objects are built faster. Or vice versa: the user pays for the game without ads and his objects are built faster.
It is worth investing in cheaper sources, such as YouTube or Yandex, where the cost of one client is cheaper than the others. To recoup advertising costs, it is recommended to set the price for displaying an advertising banner no lower than in the previously calculated CAC.